# 1. Importo librerias

In [1]:
from binance.client import Client
from datetime import datetime
from backtesting import Backtest, Strategy
from backtesting.lib import plot_heatmaps

import multiprocessing
import pandas as pd


/Users/nelsonrios/opt/anaconda3/lib/python3.8/site-packages/backtesting/_plotting.py:45: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

# 2. Configuro ambiente y traigo datos historicos

In [2]:
## necesario por cuestiones de optimizacion de performance de la simulacion
multiprocessing.set_start_method('fork', force=True)

In [139]:
#TODO: mover a variables de entorno
api_key = ''
secret_key = ''

client = Client(api_key, secret_key)


bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, "2 week ago UTC")
#bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_5MINUTE, "6 months ago UTC")

def cast_string_to_float(data):
    if type(data) == str:
        casted_data = float(data)
    else:
        casted_data = datetime.fromtimestamp(data/1000.0)
    return casted_data

# delete unwanted data - just keep date, open, high, low, close
formated_bars = []
for line in bars:
    del line[5:]
    # cast string numbers to integer
    formated_bars.append(list(map(cast_string_to_float, line)))

#  store data in a dataframe
btc_df = pd.DataFrame(formated_bars, columns=['Date', 'Open', 'High', 'Low', 'Close'])
btc_df.set_index('Date', inplace=True)
# Converting the index as date
btc_df.index = pd.to_datetime(btc_df.index)
btc_df

Open      High       Low     Close
Date                                                       
2021-06-19 21:50:00  35362.17  35418.64  35345.00  35384.01
2021-06-19 21:55:00  35384.01  35386.99  35315.86  35383.66
2021-06-19 22:00:00  35383.66  35678.15  35331.02  35582.59
2021-06-19 22:05:00  35582.58  35646.41  35542.31  35560.85
2021-06-19 22:10:00  35560.85  35588.87  35510.11  35542.63
...                       ...       ...       ...       ...
2021-06-26 21:25:00  32483.03  32580.00  32455.30  32506.74
2021-06-26 21:30:00  32506.73  32650.00  32449.54  32496.17
2021-06-26 21:35:00  32491.16  32577.36  32380.00  32407.08
2021-06-26 21:40:00  32407.08  32449.72  32140.00  32327.90
2021-06-26 21:45:00  32327.89  32328.66  31973.45  32172.75

[2016 rows x 4 columns]

# 3. Armo una estrategia de tendencia con AROON


## 3.1 Estrategia

In [140]:

from talib import AROONOSC

class AroonStrategy(Strategy):

    AROON_LENGTH = 180

    def init(self):
        price = self.data.Close
        self.arooonosc = self.I(AROONOSC, self.data.High, self.data.Low, timeperiod = self.AROON_LENGTH)

    def next(self):
        if (self.position):
            if (self.position.is_long and not self.isMarketUptrending()):
                self.sell()
            elif (self.position.is_short and not self.isMarketDowntrending()):
                self.buy()
        else:
            if (self.isVolatilityLow()):
                if (self.isMarketUptrending() and self.hasPriceUpMomentum()):
                    #self.buy(sl=self.data.Close * (1-self.STOP_LOSS/1000))
                    self.buy()
                elif (self.isMarketDowntrending() and self.hasPriceDownMomentum()):
                    #self.sell(sl=self.data.Close * (1+self.STOP_LOSS/1000))
                    self.sell()
                #else: non trending market strategy
            #else : high volatility market strategy

    def isMarketUptrending(self):
        return (self.arooonosc >=0)

    def isMarketDowntrending(self):
        return (self.arooonosc <=0)

    def hasPriceUpMomentum(self):
        return True

    def hasPriceDownMomentum(self):
        return True

    def isVolatilityLow(self):
        return True

## 3.2 Resultados

In [141]:
bt = Backtest(btc_df, AroonStrategy, cash=1000000, commission=.0004, exclusive_orders=True)
stats = bt.run()
stats

Start                     2021-06-19 21:50:00
End                       2021-06-26 21:45:00
Duration                      6 days 23:55:00
Exposure Time [%]                   90.972222
Equity Final [$]                944178.123296
Equity Peak [$]                1000988.353524
Return [%]                          -5.582188
Buy & Hold Return [%]               -9.075455
Return (Ann.) [%]                  -92.724954
Volatility (Ann.) [%]                8.048366
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -18.804176
Avg. Drawdown [%]                  -18.804176
Max. Drawdown Duration        6 days 08:45:00
Avg. Drawdown Duration        6 days 08:45:00
# Trades                                   10
Win Rate [%]                             50.0
Best Trade [%]                       7.696646
Worst Trade [%]                     -5.064623
Avg. Trade [%]                    

In [67]:
bt.plot()

/Users/nelsonrios/opt/anaconda3/lib/python3.8/site-packages/backtesting/_plotting.py:104: UserWarning: Data contains too many candlesticks to plot; downsampling to '1H'. See `Backtest.plot(resample=...)`
  warnings.warn(f"Data contains too many candlesticks to plot; downsampling to {freq!r}. "


## 3.3 Optimizacion

In [60]:
stats, heatmap = bt.optimize(AROON_LENGTH = range(175, 200),  return_heatmap=True)

In [61]:
stats

Start                     2020-06-26 19:10:00
End                       2021-06-26 19:05:00
Duration                    364 days 23:55:00
Exposure Time [%]                   99.813136
Equity Final [$]               3977965.134764
Equity Peak [$]                 4305633.50778
Return [%]                         297.796513
Buy & Hold Return [%]               243.22599
Return (Ann.) [%]                  296.298615
Volatility (Ann.) [%]              329.481494
Sharpe Ratio                         0.899288
Sortino Ratio                        7.046375
Calmar Ratio                         7.341937
Max. Drawdown [%]                  -40.357007
Avg. Drawdown [%]                   -2.585618
Max. Drawdown Duration      113 days 13:40:00
Avg. Drawdown Duration        1 days 16:14:00
# Trades                                  592
Win Rate [%]                        38.682432
Best Trade [%]                       21.41827
Worst Trade [%]                     -6.727647
Avg. Trade [%]                    

In [64]:
stats._strategy
# first iteration : <Strategy AroonStrategy(AROON_LENGTH=180)>
# second iteration : <Strategy AroonStrategy(AROON_LENGTH=180)> (BIGGER TIMEFRAME)
# third iteration : <Strategy AroonStrategy(AROON_LENGTH=194)>


<Strategy AroonStrategy(AROON_LENGTH=194)>

In [66]:
heatmap.sort_values().tail(10)

AROON_LENGTH
178             1.796759
177             1.802520
198             1.804425
181             1.814227
195             1.814690
179             1.822978
186             1.845845
187             1.846507
185             1.904431
194             2.000918
Name: SQN, dtype: float64

# 4. Evitamos trades en lateralizaciones

In [105]:
from talib import AROONOSC

class AroonFilterLateralStrategy(Strategy):

    AROON_LENGTH = 185
    AROON_UPPER_THRESHOLD = 0
    AROON_LOWER_THRESHOLD = 0

    def init(self):
        price = self.data.Close
        self.arooonosc = self.I(AROONOSC, self.data.High, self.data.Low, timeperiod = self.AROON_LENGTH)

    def next(self):
        if (self.position):
            if (self.position.is_long and not self.isMarketUptrending()):
                self.position.close()
            elif (self.position.is_short and not self.isMarketDowntrending()):
                self.position.close()
        else:
            if (self.isVolatilityLow()):
                if (self.isMarketUptrending() and self.hasPriceUpMomentum()):
                    #self.buy(sl=self.data.Close * (1-self.STOP_LOSS/1000))
                    self.buy()
                elif (self.isMarketDowntrending() and self.hasPriceDownMomentum()):
                    #self.sell(sl=self.data.Close * (1+self.STOP_LOSS/1000))
                    self.sell()
                #else: non trending market strategy
            #else : high volatility market strategy

    def isMarketUptrending(self):
        return (self.arooonosc >=0)

    def isMarketDowntrending(self):
        return (self.arooonosc <=0)

    def hasPriceUpMomentum(self):
        return (self.arooonosc >=self.AROON_UPPER_THRESHOLD)

    def hasPriceDownMomentum(self):
        return (self.arooonosc <= self.AROON_LOWER_THRESHOLD)

    def isVolatilityLow(self):
        return True

In [106]:
bt = Backtest(btc_df, AroonFilterLateralStrategy, cash=1000000, commission=.0004, exclusive_orders=True)
stats = bt.run()
stats

Start                     2021-06-19 20:40:00
End                       2021-06-26 20:35:00
Duration                      6 days 23:55:00
Exposure Time [%]                   90.724206
Equity Final [$]                935677.309752
Equity Peak [$]                1001497.099944
Return [%]                          -6.432269
Buy & Hold Return [%]              -10.600436
Return (Ann.) [%]                  -95.184646
Volatility (Ann.) [%]                5.107864
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -18.689334
Avg. Drawdown [%]                   -6.458214
Max. Drawdown Duration        6 days 07:35:00
Avg. Drawdown Duration        2 days 02:49:00
# Trades                                   10
Win Rate [%]                             50.0
Best Trade [%]                       7.494656
Worst Trade [%]                     -5.848913
Avg. Trade [%]                    

In [88]:
stats, heatmap = bt.optimize(AROON_UPPER_THRESHOLD= range(-10, 25, 5), AROON_LOWER_THRESHOLD= range(-20, 10, 5), return_heatmap=True)

In [89]:
stats

Start                     2020-12-26 20:05:00
End                       2021-06-26 20:00:00
Duration                    181 days 23:55:00
Exposure Time [%]                   99.642427
Equity Final [$]               3172536.175452
Equity Peak [$]                3472744.287096
Return [%]                         217.253618
Buy & Hold Return [%]               19.112424
Return (Ann.) [%]                  900.168654
Volatility (Ann.) [%]             1123.846477
Sharpe Ratio                         0.800971
Sortino Ratio                       17.483253
Calmar Ratio                        25.109804
Max. Drawdown [%]                  -35.849291
Avg. Drawdown [%]                   -2.604908
Max. Drawdown Duration       66 days 19:50:00
Avg. Drawdown Duration        0 days 23:51:00
# Trades                                  292
Win Rate [%]                        40.753425
Best Trade [%]                       21.78504
Worst Trade [%]                     -6.166009
Avg. Trade [%]                    

In [90]:
plot_heatmaps(heatmap, agg='mean')

Column(id='3254', ...)

In [91]:
stats._strategy
# <Strategy AroonFilterLateralStrategy(AROON_UPPER_THRESHOLD=0,AROON_LOWER_THRESHOLD=0)>



<Strategy AroonFilterLateralStrategy(AROON_UPPER_THRESHOLD=-10,AROON_LOWER_THRESHOLD=0)>

In [107]:
bt.plot()

# 5. Pruebo en otros timeframes

In [63]:
#TODO: mover a variables de entorno
api_key = ''
secret_key = ''

client = Client(api_key, secret_key)


bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_5MINUTE, "3 month ago UTC")
#bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_5MINUTE, "6 months ago UTC")

def cast_string_to_float(data):
    if type(data) == str:
        casted_data = float(data)
    else:
        casted_data = datetime.fromtimestamp(data/1000.0)
    return casted_data

# delete unwanted data - just keep date, open, high, low, close
formated_bars = []
for line in bars:
    del line[5:]
    # cast string numbers to integer
    formated_bars.append(list(map(cast_string_to_float, line)))

#  store data in a dataframe
btc_df = pd.DataFrame(formated_bars, columns=['Date', 'Open', 'High', 'Low', 'Close'])
btc_df.set_index('Date', inplace=True)
# Converting the index as date
btc_df.index = pd.to_datetime(btc_df.index)
btc_df

Open      High       Low     Close
Date                                                       
2021-03-27 12:35:00  54833.40  54884.19  54800.13  54824.86
2021-03-27 12:40:00  54822.12  54885.74  54708.62  54791.22
2021-03-27 12:45:00  54791.22  54882.63  54770.31  54871.45
2021-03-27 12:50:00  54871.45  54971.59  54858.68  54872.46
2021-03-27 12:55:00  54872.45  54996.99  54869.70  54961.85
...                       ...       ...       ...       ...
2021-06-27 12:10:00  33193.26  33213.33  33088.88  33149.00
2021-06-27 12:15:00  33149.98  33159.13  32868.69  32969.78
2021-06-27 12:20:00  32969.77  33075.00  32958.67  32979.35
2021-06-27 12:25:00  32979.36  33220.00  32964.38  33195.85
2021-06-27 12:30:00  33195.85  33260.00  33128.43  33136.20

[26410 rows x 4 columns]

In [157]:
from talib import AROONOSC

class AroonStrategyTakeProfit(Strategy):

    AROON_LENGTH = 180

    UPPER_THRESHOLD = 91
    TAKE_PROFIT_UP_THRESHOLD = 12

    LOWER_THRESHOLD = -16
    TAKE_PROFIT_DOWN_THRESHOLD = -12

    STOP_LOSS = 35 # 3.5%

    #def COV(self, array, n):
    #    return pd.Series(array).rolling(n).std() / pd.Series(array).rolling(n).mean()


    def init(self):
        price = self.data.Close
        self.arooonosc = self.I(AROONOSC, self.data.High, self.data.Low, timeperiod = self.AROON_LENGTH)
        self.rsi = self.I(self.RSI, price)

    def next(self):
        if (self.position):
            if (self.position.is_long and not self.isMarketUptrending()):
                self.position.close()
            elif (self.position.is_short and not self.isMarketDowntrending()):
                self.position.close()
        else:
            if (self.isVolatilityLow()):
                if (self.hasPriceUpMomentum()):
                    self.buy(sl=self.data.Close * (1-self.STOP_LOSS/1000))
                    #self.buy()
                elif (self.hasPriceDownMomentum()):
                    self.sell(sl=self.data.Close * (1+self.STOP_LOSS/1000))
                    #self.sell()
                #else: non trending market strategy
            #else : high volatility market strategy

    def isMarketUptrending(self):
        return (self.arooonosc >= self.TAKE_PROFIT_UP_THRESHOLD)

    def isMarketDowntrending(self):
        return (self.arooonosc <= self.TAKE_PROFIT_DOWN_THRESHOLD)

    def hasPriceUpMomentum(self):
        return (self.arooonosc >=self.UPPER_THRESHOLD)

    def hasPriceDownMomentum(self):
        return (self.arooonosc <=self.LOWER_THRESHOLD)

    def isVolatilityLow(self):
        return True

In [159]:
bt = Backtest(btc_df, AroonStrategyTakeProfit, cash=1000000, commission=.0004, exclusive_orders=True, margin=0.333)
stats = bt.run()
stats

Start                     2021-03-27 12:35:00
End                       2021-06-27 12:30:00
Duration                     91 days 23:55:00
Exposure Time [%]                   70.984476
Equity Final [$]               8352873.031064
Equity Peak [$]               10454115.832158
Return [%]                         735.287303
Buy & Hold Return [%]                -39.5599
Return (Ann.) [%]               414813.937209
Volatility (Ann.) [%]          2236515.565181
Sharpe Ratio                         0.185473
Sortino Ratio                     4612.087482
Calmar Ratio                      9151.856985
Max. Drawdown [%]                  -45.325658
Avg. Drawdown [%]                   -5.801739
Max. Drawdown Duration       28 days 17:10:00
Avg. Drawdown Duration        0 days 17:36:00
# Trades                                  104
Win Rate [%]                        43.269231
Best Trade [%]                      16.148805
Worst Trade [%]                     -3.554203
Avg. Trade [%]                    

In [138]:
stats._trades.sort_values('ReturnPct').head(10)

Size  EntryBar  ExitBar    EntryPrice    ExitPrice           PnL  \
98    -70     24908    24997  31731.732228  32859.54225 -78946.701540   
33    -20      8329     8370  48572.483232  50293.24785 -34415.292360   
61    -26     14625    14644  42422.944032  43925.32755 -39061.971468   
84    -46     20446    20484  35253.303036  36501.76935 -57429.450444   
101    58     25674    25725  35432.797452  34178.97795 -72721.531116   
65    -30     15508    15553  39994.935624  41401.87335 -42208.131780   
26     18      6468     6612  57201.141308  55667.44000 -27606.623544   
52     15     12434    12534  59039.496356  57522.11000 -22760.795340   
62    -24     14645    14746  44012.378004  45033.92000 -24517.007904   
50     16     11988    12023  59347.409472  58055.58000 -20669.271552   

     ReturnPct           EntryTime            ExitTime        Duration  
98   -0.035542 2021-06-22 07:25:00 2021-06-22 14:50:00 0 days 07:25:00  
33   -0.035427 2021-04-25 17:50:00 2021-04-25 21:15:00 0 days 03:25:00  
61   -0.035414 2021-05-17 14:30:00 2021-05-17 16:05:00 0 days 01:35:00  
84   -0.035414 2021-06-06 19:35:00 2021-06-06 22:45:00 0 days 03:10:00  
101  -0.035386 2021-06-24 23:15:00 2021-06-25 03:30:00 0 days 04:15:00  
65   -0.035178 2021-05-20 16:05:00 2021-05-20 19:50:00 0 days 03:45:00  
26   -0.026812 2021-04-18 23:35:00 2021-04-19 11:35:00 0 days 12:00:00  
52   -0.025701 2021-05-09 23:55:00 2021-05-10 08:15:00 0 days 08:20:00  
62   -0.023210 2021-05-17 16:10:00 2021-05-18 00:35:00 0 days 08:25:00  
50   -0.021767 2021-05-08 10:45:00 2021-05-08 13:40:00 0 days 02:55:00

In [147]:
bt.plot()

/Users/nelsonrios/opt/anaconda3/lib/python3.8/site-packages/backtesting/_plotting.py:104: UserWarning: Data contains too many candlesticks to plot; downsampling to '15T'. See `Backtest.plot(resample=...)`
  warnings.warn(f"Data contains too many candlesticks to plot; downsampling to {freq!r}. "


In [130]:
stats, heatmap = bt.optimize( STOP_LOSS = range(10, 60), return_heatmap=True)

In [131]:
stats

Start                     2021-03-27 12:35:00
End                       2021-06-27 12:30:00
Duration                     91 days 23:55:00
Exposure Time [%]                   70.984476
Equity Final [$]                2252215.21104
Equity Peak [$]                2420216.262176
Return [%]                         125.221521
Buy & Hold Return [%]                -39.5599
Return (Ann.) [%]                 2320.466187
Volatility (Ann.) [%]             1679.684882
Sharpe Ratio                         1.381489
Sortino Ratio                       76.327869
Calmar Ratio                       126.162012
Max. Drawdown [%]                  -18.392749
Avg. Drawdown [%]                   -2.214098
Max. Drawdown Duration       25 days 14:00:00
Avg. Drawdown Duration        0 days 18:21:00
# Trades                                  104
Win Rate [%]                        43.269231
Best Trade [%]                      16.148805
Worst Trade [%]                     -3.554203
Avg. Trade [%]                    

In [133]:
stats._strategy
# <Strategy AroonStrategy1min(UPPER_THRESHOLD=83,LOWER_THRESHOLD=-28)>
heatmap.sort_values().tail(10)

STOP_LOSS
27           2.412591
56           2.416680
55           2.419308
28           2.429800
40           2.432208
37           2.432419
39           2.454920
38           2.459758
36           2.465639
35           2.468418
Name: SQN, dtype: float64

In [116]:
plot_heatmaps(heatmap, agg='mean')

Column(id='19236', ...)

In [117]:
bt.plot()

/Users/nelsonrios/opt/anaconda3/lib/python3.8/site-packages/backtesting/_plotting.py:104: UserWarning: Data contains too many candlesticks to plot; downsampling to '15T'. See `Backtest.plot(resample=...)`
  warnings.warn(f"Data contains too many candlesticks to plot; downsampling to {freq!r}. "
